In [75]:
import numpy as np
import json

In [167]:
with open("input.json", "r") as read_file:
    data = json.load(read_file)
data

{'world': {'size': {'N': 4, 'M': 3},
  'states': {'S': [1, 1], 'T': [[4, 2], [4, 3]], 'F': [[2, 2]], 'B': []}},
 'transition_rates': {'p1': 0.8, 'p2': 0.1, 'p3': 0.1},
 'reward_function': {'r': -0.04, 'r_T': [-1.0, 1.0], 'r_B': []},
 'disc': 1.0}

In [168]:
class MarkovDecisionProcess:
    def __init__(self, *, N, M, S, T, F, B, p1, p2, p3, r, r_T, r_B, disc):
        self.N, self.M = N, M
        self.S = S
        self.T = self.lists_to_tuples(T)
        self.F = self.lists_to_tuples(F)
        self.B = self.lists_to_tuples(B)
        self.p1, self.p2, self.p3 = p1, p2, p3
        self.r, self.r_T, self.r_B = r, r_T, r_B
        self.disc = disc  # discounting
        assert len(self.T) == len(self.r_T) 
        assert len(self.B) == len(self.r_B)
        
    def lists_to_tuples(self, I):
        return [(a, b) for a, b in I]


MDP = MarkovDecisionProcess(**data['world']['size'],
                            **data['world']['states'],
                            **data['transition_rates'],
                            **data['reward_function'],
                            disc=data['disc'])

In [245]:
class World:
    def __init__(self):  # S = (1,1), T = [(1,4), (5,2)], F = [(4,2)], B
        self.grid = [[State(x, y) for y in range(1, MDP.M + 1)] for x in range(1, MDP.N + 1)]
        
        self.get_state(*MDP.S).kind = 'S'
    
        for t, rt in zip(MDP.T, MDP.r_T):
            self.get_state(*t).kind = 'T'
            self.get_state(*t).reward = rt
        for b, rb in zip(MDP.B, MDP.r_B):
            self.get_state(*b).kind = 'B'
            self.get_state(*b).reward = rb
        for f in MDP.F:
            self.get_state(*f).kind = 'F'
            
    def get_state(self, x, y):
        return self.grid[x-1][y-1]
        
    def print_utility(self):
        pass
    
    def print_policy(self):
        pass
    
    
class State:
    def __init__(self, x, y, kind="N", reward=MDP.r):
        self.x, self.y = x, y
        self.kind = kind  # S/T/F/B
        self.reward = reward
        self.utility = np.random.random() - 0.5
        self.policy = " "

    def invalid_state(self, x, y):
        out_of_world = x < 1 or x > MDP.N or y < 1 or y > MDP.M
        return (x, y) in MDP.F or out_of_world
    
    def move(self, action):
        if action == 'U':
            dst_x = self.x
            dst_y = self.y + 1
        if action == 'L':
            dst_x = self.x - 1
            dst_y = self.y
        if action == 'R':
            dst_x = self.x + 1
            dst_y = self.y
        if action == 'D':
            dst_x = self.x
            dst_y = self.y - 1
        if self.invalid_state(dst_x, dst_y):
            return self.x, self.y
        else:
            return dst_x, dst_y
        
    def transitions(self):
        probabilities = [MDP.p1, MDP.p2, MDP.p3, 1 - (MDP.p1 + MDP.p2 + MDP.p3)]
        neigh_coordinates = [(self.x - 1, self.y), (self.x, self.y + 1),
                             (self.x + 1, self.y), (self.x, self.y - 1)]
        transitions = []
        for move in ['U', 'L', 'R', 'D']:
            if move == 'U':
                destination = (self.x, self.y + 1)
                left = (self.x - 1, self.y)
                right = (self.x + 1, self.y)
                opposite = (self.x, self.y - 1)
            
            if move == 'L':
                destination = (self.x - 1, self.y)
                left = (self.x, self.y - 1)
                right = (self.x, self.y + 1)
                opposite = (self.x + 1, self.y)
                
            if move == 'D':
                destination = (self.x, self.y - 1)
                left = (self.x + 1, self.y)
                right = (self.x - 1, self.y)
                opposite = (self.x, self.y + 1)
            
            if move == 'R':
                destination = (self.x + 1, self.y)
                left = (self.x, self.y + 1)
                right = (self.x, self.y - 1)
                opposite = (self.x - 1, self.y)
                
            for coordinates, transition_rate in zip([destination, left, right, opposite], probabilities):
                if self.invalid_state(*coordinates):
                    coordinates = self.x, self.y
                transitions.append((move, coordinates, transition_rate))
        return transitions
                
from copy import copy, deepcopy
from itertools import groupby
        
class ValueIteration:
    def __init__(self, stopping_condition=0.0001):
        self.stop_cond = stopping_condition
        self.t = 0
        self.converged = False
        
    def iterate(self):
        prev_world = World()
        while not self.converged:
            self.converged = True
            self.t += 1
            updated_world = deepcopy(prev_world)
            for x in range(1, MDP.N + 1):
                for y in range(1, MDP.M + 1):
                    if (x, y) not in MDP.F:
                        s = updated_world.get_state(x, y)
                        if s.kind != 'T':
                            prev_utility = s.utility
                            max_sum, action = self.select_action(prev_world, s.transitions())
                            dest_state = prev_world.get_state(*s.move(action))
                            if dest_state.kind == 'T':
                                reward = dest_state.utility
                            else:
                                reward = dest_state.reward
                            s.utility = reward + MDP.disc * max_sum  # NIE s.reward ale reward pola wskazanego przez akcje "move"
                            print(self.t, s.utility, prev_utility, f"({x}, {y})")
                            if abs(s.utility - prev_utility) >= self.stop_cond:
                                self.converged = False
            prev_world = updated_world
        return updated_world
    
    def select_action(self, world, transitions):
        sums = []
        for move, group in groupby(transitions, lambda x: x[0]):
            sum_ = 0
            for transition in group:
                sum_ += world.get_state(*transition[1]).utility * transition[2]
            sums.append((sum_, move))
        return max(sums, key=lambda x: x[0])
                

In [246]:
w = World()
# t = w.get_state(4,3).transitions()
vi = ValueIteration(stopping_condition=0.0001)
vi.iterate()

1 0.09547931214721228 -0.3271936987310399 (1, 1)
1 0.08388355051276034 0.24722479489197458 (1, 2)
1 0.30072184655126594 -0.4117691552771535 (1, 3)
1 0.2487710987223787 -0.295811538932634 (2, 1)
1 0.2801777850006824 0.4464703532372297 (2, 3)
1 0.30258169310041316 0.43491675813613184 (3, 1)
1 0.29771150738664626 -0.3148964094213277 (3, 2)
1 0.289865059586265 0.04178417938613954 (3, 3)
1 0.35343058881355005 0.24229440484771025 (4, 1)
2 0.17695316524390023 0.09547931214721228 (1, 1)
2 0.2173541873435648 0.08388355051276034 (1, 2)
2 0.25866744039620765 0.30072184655126594 (1, 3)
2 0.25181957422480633 0.2487710987223787 (2, 1)
2 0.2566130342411493 0.2801777850006824 (2, 3)
2 0.302773791099546 0.30258169310041316 (3, 1)
2 0.25741388117798486 0.29771150738664626 (3, 2)
2 0.2428998846978371 0.289865059586265 (3, 3)
2 0.3083456992422364 0.35343058881355005 (4, 1)
3 0.20088639463859156 0.17695316524390023 (1, 1)
3 0.21040478978567909 0.2173541873435648 (1, 2)
3 0.21846199978070183 0.2586674403962

49 0.11579869201603915 0.15101538225141733 (1, 1)
49 0.10739063775089805 0.13289165974882092 (1, 2)
49 0.08750582033201462 0.099123564040932 (1, 3)
49 0.1197404329604006 0.15925998477001915 (2, 1)
49 0.08254537993399588 0.1128013612886469 (2, 3)
49 0.3560672515892637 0.15986054500799599 (3, 1)
49 0.32315278068888387 0.4183357346606887 (3, 2)
49 0.30037505753844285 0.12498138459533312 (3, 3)
49 0.36179631839506815 0.422809529527994 (4, 1)
50 0.07811127934501422 0.11579869201603915 (1, 1)
50 0.07411708116301094 0.10739063775089805 (1, 2)
50 0.0629176302273195 0.08750582033201462 (1, 3)
50 0.26880188786349113 0.1197404329604006 (2, 1)
50 0.21680912201755345 0.08254537993399588 (2, 3)
50 0.3173590579438693 0.3560672515892637 (3, 1)
50 0.2984368211601729 0.32315278068888387 (3, 2)
50 0.22120309622553389 0.30037505753844285 (3, 3)
50 0.3212234117144877 0.36179631839506815 (4, 1)
51 0.19026434634159542 0.07811127934501422 (1, 1)
51 0.037312439708613566 0.07411708116301094 (1, 2)
51 0.14715076

95 0.11859819059306714 0.12270581671613928 (1, 3)
95 0.19849548396933075 0.23637620461256945 (2, 1)
95 0.14115622979938658 0.16795025537883523 (2, 3)
95 0.1994512664133769 0.23902530380852108 (3, 1)
95 0.1955494133505824 0.23061428483892013 (3, 2)
95 0.1557127870900468 0.1844577234045244 (3, 3)
95 0.200450751373064 0.240609134435791 (4, 1)
96 0.15101552895560405 0.18075595055912766 (1, 1)
96 0.13289185389575545 0.1414354672422665 (1, 2)
96 0.09912381583305857 0.11859819059306714 (1, 3)
96 0.1592601099245677 0.19849548396933075 (2, 1)
96 0.11280147563191475 0.14115622979938658 (2, 3)
96 0.15986066907484714 0.1994512664133769 (3, 1)
96 0.41833575810806595 0.1955494133505824 (3, 2)
96 0.12498148734143172 0.1557127870900468 (3, 3)
96 0.4228095545363677 0.200450751373064 (4, 1)
97 0.1157988262247901 0.15101552895560405 (1, 1)
97 0.10739079394363432 0.13289185389575545 (1, 2)
97 0.08750601226310167 0.09912381583305857 (1, 3)
97 0.11974055724479127 0.1592601099245677 (2, 1)
97 0.0825454849995

137 0.19554941335078246 0.2306142848391273 (3, 2)
137 0.15571278709024322 0.18445772340474265 (3, 3)
137 0.20045075137328833 0.2406091344360153 (4, 1)
138 0.15101552895586623 0.18075595055943974 (1, 1)
138 0.13289185389610236 0.1414354672427529 (1, 2)
138 0.09912381583350857 0.11859819059343982 (1, 3)
138 0.1592601099247914 0.1984954839695587 (2, 1)
138 0.11280147563211909 0.14115622979962258 (2, 3)
138 0.15986066907506888 0.19945126641359953 (3, 1)
138 0.41833575810810786 0.19554941335078246 (3, 2)
138 0.12498148734161538 0.15571278709024322 (3, 3)
138 0.42280955453641234 0.20045075137328833 (4, 1)
139 0.11579882622502999 0.15101552895586623 (1, 1)
139 0.10739079394391346 0.13289185389610236 (1, 2)
139 0.08750601226344465 0.09912381583350857 (1, 3)
139 0.1197405572450134 0.1592601099247914 (2, 1)
139 0.08254548499971612 0.11280147563211909 (2, 3)
139 0.35606728634744755 0.15986066907506888 (3, 1)
139 0.32315282212815477 0.41833575810810786 (3, 2)
139 0.3003750877307254 0.1249814873416

180 0.41833575810810786 0.19554941335078246 (3, 2)
180 0.12498148734161538 0.15571278709024322 (3, 3)
180 0.42280955453641234 0.20045075137328833 (4, 1)
181 0.11579882622502999 0.15101552895586623 (1, 1)
181 0.10739079394391346 0.13289185389610236 (1, 2)
181 0.08750601226344465 0.09912381583350857 (1, 3)
181 0.1197405572450134 0.1592601099247914 (2, 1)
181 0.08254548499971612 0.11280147563211909 (2, 3)
181 0.35606728634744755 0.15986066907506888 (3, 1)
181 0.32315282212815477 0.41833575810810786 (3, 2)
181 0.3003750877307254 0.12498148734161538 (3, 3)
181 0.3617963409026447 0.42280955453641234 (4, 1)
182 0.07811140781290507 0.11579882622502999 (1, 1)
182 0.0741172197688067 0.10739079394391346 (1, 2)
182 0.06291778488144684 0.08750601226344465 (1, 3)
182 0.2688019405269607 0.1197405572450134 (2, 1)
182 0.21680916718452356 0.08254548499971612 (2, 3)
182 0.317359083569676 0.35606728634744755 (3, 1)
182 0.29843685311064705 0.32315282212815477 (3, 2)
182 0.2212031398835226 0.300375087730725

...

10268 0.29843685311064705 0.32315282212815477 (3, 2)
10268 0.2212031398835226 0.3003750877307254 (3, 3)
10268 0.321223435447125 0.3617963409026447 (4, 1)
10269 0.19026441517973974 0.07811140781290507 (1, 1)
10269 0.0373125702040854 0.0741172197688067 (1, 2)
10269 0.14715083421264422 0.06291778488144684 (1, 3)
10269 0.267647654961133 0.2688019405269607 (2, 1)
10269 0.1803243453437228 0.21680916718452356 (2, 3)
10269 0.2785583420257323 0.317359083569676 (3, 1)
10269 0.264998693986679 0.29843685311064705 (3, 2)
10269 0.21485673288799714 0.2212031398835226 (3, 3)
10269 0.28083700025938013 0.321223435447125 (4, 1)
10270 0.19687582250728894 0.19026441517973974 (1, 1)
10270 0.11967404618460889 0.0373125702040854 (1, 2)
10270 0.1227058167166512 0.14715083421264422 (1, 3)
10270 0.23637620461281247 0.267647654961133 (2, 1)
10270 0.1679502553791423 0.1803243453437228 (2, 3)
10270 0.23902530380874523 0.2785583420257323 (3, 1)
10270 0.2306142848391273 0.264998693986679 (3, 2)
10270 0.18445772340474

10325 0.19945126641359953 0.23902530380874523 (3, 1)
10325 0.19554941335078246 0.2306142848391273 (3, 2)
10325 0.15571278709024322 0.18445772340474265 (3, 3)
10325 0.20045075137328833 0.2406091344360153 (4, 1)
10326 0.15101552895586623 0.18075595055943974 (1, 1)
10326 0.13289185389610236 0.1414354672427529 (1, 2)
10326 0.09912381583350857 0.11859819059343982 (1, 3)
10326 0.1592601099247914 0.1984954839695587 (2, 1)
10326 0.11280147563211909 0.14115622979962258 (2, 3)
10326 0.15986066907506888 0.19945126641359953 (3, 1)
10326 0.41833575810810786 0.19554941335078246 (3, 2)
10326 0.12498148734161538 0.15571278709024322 (3, 3)
10326 0.42280955453641234 0.20045075137328833 (4, 1)
10327 0.11579882622502999 0.15101552895586623 (1, 1)
10327 0.10739079394391346 0.13289185389610236 (1, 2)
10327 0.08750601226344465 0.09912381583350857 (1, 3)
10327 0.1197405572450134 0.1592601099247914 (2, 1)
10327 0.08254548499971612 0.11280147563211909 (2, 3)
10327 0.35606728634744755 0.15986066907506888 (3, 1)


10364 0.2212031398835226 0.3003750877307254 (3, 3)
10364 0.321223435447125 0.3617963409026447 (4, 1)
10365 0.19026441517973974 0.07811140781290507 (1, 1)
10365 0.0373125702040854 0.0741172197688067 (1, 2)
10365 0.14715083421264422 0.06291778488144684 (1, 3)
10365 0.267647654961133 0.2688019405269607 (2, 1)
10365 0.1803243453437228 0.21680916718452356 (2, 3)
10365 0.2785583420257323 0.317359083569676 (3, 1)
10365 0.264998693986679 0.29843685311064705 (3, 2)
10365 0.21485673288799714 0.2212031398835226 (3, 3)
10365 0.28083700025938013 0.321223435447125 (4, 1)
10366 0.19687582250728894 0.19026441517973974 (1, 1)
10366 0.11967404618460889 0.0373125702040854 (1, 2)
10366 0.1227058167166512 0.14715083421264422 (1, 3)
10366 0.23637620461281247 0.267647654961133 (2, 1)
10366 0.1679502553791423 0.1803243453437228 (2, 3)
10366 0.23902530380874523 0.2785583420257323 (3, 1)
10366 0.2306142848391273 0.264998693986679 (3, 2)
10366 0.18445772340474265 0.21485673288799714 (3, 3)
10366 0.24060913443601

10409 0.14115622979962258 0.1679502553791423 (2, 3)
10409 0.19945126641359953 0.23902530380874523 (3, 1)
10409 0.19554941335078246 0.2306142848391273 (3, 2)
10409 0.15571278709024322 0.18445772340474265 (3, 3)
10409 0.20045075137328833 0.2406091344360153 (4, 1)
10410 0.15101552895586623 0.18075595055943974 (1, 1)
10410 0.13289185389610236 0.1414354672427529 (1, 2)
10410 0.09912381583350857 0.11859819059343982 (1, 3)
10410 0.1592601099247914 0.1984954839695587 (2, 1)
10410 0.11280147563211909 0.14115622979962258 (2, 3)
10410 0.15986066907506888 0.19945126641359953 (3, 1)
10410 0.41833575810810786 0.19554941335078246 (3, 2)
10410 0.12498148734161538 0.15571278709024322 (3, 3)
10410 0.42280955453641234 0.20045075137328833 (4, 1)
10411 0.11579882622502999 0.15101552895586623 (1, 1)
10411 0.10739079394391346 0.13289185389610236 (1, 2)
10411 0.08750601226344465 0.09912381583350857 (1, 3)
10411 0.1197405572450134 0.1592601099247914 (2, 1)
10411 0.08254548499971612 0.11280147563211909 (2, 3)
1

KeyboardInterrupt: 

In [240]:
from itertools import cycle, islice

In [241]:
a = [1,2,3,4]
ac = cycle(a)

In [242]:
list(islice(ac, 1, 5))

[2, 3, 4, 1]

In [243]:
World().get_state(4,3).utility

-0.3559900326747665

In [244]:
for j in reversed(range(1, MDP.M + 1)):
    for i in range(1, MDP.N + 1):
        print("{:2f}".format(vi.W.get_state(i,j).utility), end=' ');
    print(end='\n')

print()

for j in reversed(range(1, MDP.M + 1)):
    for i in range(1, MDP.N + 1):
        print(vi.W.get_state(i,j).policy, end='');
    print(end='\n')

print()
    
for j in reversed(range(1, MDP.M + 1)):
    for i in range(1, MDP.N + 1):
        print((i,j), end='');
    print(end='\n')

AttributeError: 'ValueIteration' object has no attribute 'W'

In [177]:
0.538199 0.594432 0.644432 0.693601 
0.488239 0.540440 0.651081 0.707386 
0.505193 0.557296 0.607294 0.651820

SyntaxError: invalid syntax (<ipython-input-177-dc2b36651629>, line 1)